# Voting

In [1]:
# Importing the libraries
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

# Importing the dataset
dataset = pd.read_csv('CVD dataset8.csv')
data=dataset.iloc[:, :].values
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, 8].values
# X = dataset.iloc[:, [ 0, 1, 2, 5, 10, 11, 13, 15]].values

rows = len(data)    # 3 rows in your example
cols = len(data[0])
print(rows)
print(cols)

560
9


In [2]:
dataNoCvd = data[~(data[:,8] > 0.0)]
dataCvd = data[~(data[:,8] < 1.0)]
rowsNoCvd = len(dataNoCvd)    
rowsCvd = len(dataCvd)
print(rowsNoCvd)
print(rowsCvd)
# print(dataNoCvd)
# print(dataCvd)

519
41


In [3]:
def find_NoCvd_limitsArray(i,DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue):
    if i>0 :
        DownNoCvd = UpNoCvd
        UpNoCvd= fold_NoCvd_total+UpNoCvd
    if i < fold_NoCvd_residue :
        UpNoCvd+= 1
#     print("NoCvd limits, Down :",DownNoCvd,"Up ",UpNoCvd)
    return   DownNoCvd, UpNoCvd   
 
def find_Cvd_limitsArray(i,DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv):
    if i>0 :
        DownCvd = UpCvd
        UpCvd= fold_Cvd_total+UpCvd
    if i >= cv - fold_Cvd_residue :
         UpCvd+= 1     
#     print("Cvd limits, Down :",DownCvd,"Up ",UpCvd)
    return   DownCvd, UpCvd  

def find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1=dataNoCvd[DownNoCvd:UpNoCvd,:]
    temp2=dataCvd[DownCvd:UpCvd,:]
    temp3=np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

def find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1 = np.delete(dataNoCvd, slice(DownNoCvd, UpNoCvd), axis=0)
    temp2 = np.delete(dataCvd, slice(DownCvd, UpCvd), axis=0)
    temp3 = np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

In [4]:
def create_train_test_sets(cv,dataNoCvd,dataCvd):
    test_total = []
    train_total = []
    train_total_Cvd = []
    train_total_NoCvd = []
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)

    fold_Cvd_total = rowsCvd//cv
    fold_Cvd_residue= rowsCvd%cv
    print("fold_Cvd_total  :",fold_Cvd_total," fold_Cvd_residue  :",fold_Cvd_residue)

    fold_NoCvd_total = rowsNoCvd//cv
    fold_NoCvd_residue= rowsNoCvd%cv
    print("fold_NoCvd_total:",fold_NoCvd_total,"fold_NoCvd_residue:",fold_NoCvd_residue)

    DownNoCvd=0
    DownCvd=0
    UpNoCvd = fold_NoCvd_total
    UpCvd = fold_Cvd_total

    for i in range(cv):
        X_test = []
        y_test = []
        X_train = []
        y_train = []
#         print("============",i,"==============")
        DownNoCvd, UpNoCvd = find_NoCvd_limitsArray(i, DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue)
        DownCvd, UpCvd = find_Cvd_limitsArray(i, DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv)

        testSubset_NoCvd ,testSubset_Cvd ,testSubset_total = find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
        trainSubset_NoCvd ,trainSubset_Cvd ,trainSubset_total = find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
     
    #creating X_train, y_train, X_test, y_test
        X_test.append(np.delete(testSubset_total, 8, axis=1))
        y_test_temp = np.delete(testSubset_total, slice(0, 8), axis=1)
        y_test.append(np.reshape(y_test_temp, len(y_test_temp)))
        X_test_temp = np.array(X_test)
        X_test = X_test_temp[0]
        y_test_temp = np.array(y_test)
        y_test = y_test_temp[0]
    
        X_train.append(np.delete(trainSubset_total, 8, axis=1))
        y_train_temp = np.delete(trainSubset_total, slice(0, 8), axis=1)
        y_train.append(np.reshape(y_train_temp, len(y_train_temp)))
        X_train_temp = np.array(X_train)
        X_train = X_train_temp[0]
        y_train_temp = np.array(y_train)
        y_train = y_train_temp[0]
        
    #add every subset in a list so we can handle thm later 
        test_total.append([X_test,y_test])
        train_total.append([X_train,y_train]) 
        train_total_NoCvd.append(trainSubset_NoCvd)
        train_total_Cvd.append(trainSubset_Cvd)
    return train_total, test_total, train_total_NoCvd, train_total_Cvd

In [5]:
train_total, test_total, train_total_NoCvd, train_total_Cvd = create_train_test_sets(10,dataNoCvd,dataCvd)

fold_Cvd_total  : 4  fold_Cvd_residue  : 1
fold_NoCvd_total: 51 fold_NoCvd_residue: 9


In [6]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
    print(len(train_total[i][0]))
    ratio = find_ratio(train_total[i])
    print("ratio in train set:", ratio)
    ratio = find_ratio(test_total[i])
    print("ratio in test set:", ratio)

504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07142857142857142
ratio in test set: 0.08928571428571429


In [7]:
from xgboost import XGBClassifier


def my_fit(ratio,dataNoCvd,dataCvd,params):   
    Subarray=[]
    models = []
    # yarray
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)
#     print("Size of NoCvd cases in train set:",rowsNoCvd)
#     print("Size of Cvd cases in train set  :",rowsCvd)


    numOfSubsamples = rowsNoCvd//(rowsCvd*ratio)
    numOfSubsamples= int(numOfSubsamples)
    SubNoCvd = rowsNoCvd//numOfSubsamples
    residue = rowsNoCvd- SubNoCvd*numOfSubsamples


    Up = 0


    for i in range(numOfSubsamples):
        
        classifier = XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=params[5],
                  colsample_bynode=1, colsample_bytree=1, gamma=params[4],
                  learning_rate=params[0], max_delta_step=0, max_depth=params[1],
                  min_child_weight=params[3], missing=None, n_estimators=params[2], n_jobs=1,
                  nthread=None, objective='binary:logistic', random_state=0,
                  reg_alpha=0, reg_lambda=params[6], scale_pos_weight=params[7], seed=None,
                  silent=None, subsample=1.0, verbosity=1)
    #     print(i)
    #Creating the training set for each model
        Down = Up
        Up= Up + SubNoCvd
        if i < residue :
            Up+= 1
        
#         print(Down)
#         print(Up)
        
        Sub1=dataNoCvd[Down:Up,:]
        Sub2=np.concatenate((Sub1, dataCvd))
        Subarray.append(Sub2)
        
    #Dividing to X and y of the previous traing set    
        X=np.delete(Subarray[i], 8, axis=1)
        y=np.delete(Subarray[i], slice(0, 8), axis=1)
        y=np.reshape(y, len(y))
        
        classifier.fit( X, y)
        models.append(classifier)
    return models     

In [8]:

def voting(models,X):
    y_pred = []
    y_pred_models = []

    models_size = len(models)
    X_size = len(X)
            
    for i in range(models_size):
        y_pred_models.append(models[i].predict(X))
        
    for j in range(X_size):
        case = 0
        for i in range(models_size):
            if y_pred_models[i][j] == 1.0:
                case+=1
        if case >  models_size/2 :
            y_pred.append(1.) 
        else:
            y_pred.append(0.) 
            
    return y_pred        
     

In [9]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from sklearn import metrics

def my_cross_val( cv, train_total, test_total, train_total_NoCvd, train_total_Cvd,params):
    accuracy = []
    specificity = []
    sensitivity = []
    auc = []
    
    # print(X)
    for i in range(cv):
#         X_train = train_total[i][0]
#         y_train = train_total[i][1]
        X_test = test_total[i][0]
        y_test = test_total[i][1]
        


        models = my_fit( 1, train_total_NoCvd[i], train_total_Cvd[i],params)


        y_pred = voting(models,X_test)

        cm = confusion_matrix(y_test, y_pred)
    #     print(cm)

        total1=sum(sum(cm))
        #####from confusion matrix calculate accuracy
        accuracy1=(cm[0,0]+cm[1,1])/total1
    #   print ('Accuracy : ', accuracy1)

        specificity1 = cm[0,0]/(cm[0,0]+cm[0,1])
    #   print('Specificity : ', specificity1 )

        sensitivity1 = cm[1,1]/(cm[1,0]+cm[1,1])
    #   print('Sensitivity : ', sensitivity1)
        
#         y = np.array(y_test)
#         pred = np.array(y_pred)
#         fpr, tpr, thresholds = metrics.roc_curve(y, pred, pos_label=2)
#         auc1 = metrics.auc(fpr, tpr)
        
        auc1 = roc_auc_score(y_test, y_pred)

    
        accuracy.append(accuracy1)
        specificity.append(specificity1)
        sensitivity.append(sensitivity1) 
        auc.append(auc1)
    return accuracy, specificity, sensitivity, auc

In [10]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[ 0.1],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[200],
                     "subsample"       :[1.0],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5], #0.5-1
                     "reg_lambda"      :[1.5], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[6]
        }

In [62]:
parameters : [0.1, 4, 200, 1.0, 0, 0.5, 1.5, 6]
accuracy : 0.675
spes     : 0.6744343891402715
sens     : 0.69
auc      : 0.6822171945701357

0.7099095022624434

In [14]:
comb = compute_comb(params)
print(comb[0])
accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,comb[0])

[0.1, 4, 200, 1.0, 0, 0.5, 1.5, 6]


In [15]:
print(mean(accuracy))
print(mean(specificity))
print(mean(sensitivity))
print(mean(auc))

0.675
0.6744343891402715
0.69
0.6822171945701357


In [10]:
# https://www.geeksforgeeks.org/python-all-possible-permutations-of-n-lists/

def compute_comb(params):
    
    # initializing lists 
    list1 = params.get("learning_rate")
    list2 = params.get("max_depth")
    list3 = params.get("n_estimators") 
    list4 = params.get("min_child_weight")
    list5 = params.get("gamma")    
    list6 = params.get("colsample_bytree")
    list7 = params.get("reg_lambda") 
    list8 = params.get("scale_pos_weight")

#     # printing lists  
#     print ("The original lists are : " + str(list1) +
#                                    " " + str(list2) + 
#                                    " " + str(list3) + 
#                                    " " + str(list4) + 
#                                    " " + str(list5) + 
#                                    " " + str(list6) +
#                                    " " + str(list7) +
#                                    " " + str(list8)) 

    # using list comprehension  
    # to compute all possible permutations 
    res = [[i, j, k, l, m, n, o, p] for i in list1  
                                    for j in list2 
                                    for k in list3 
                                    for l in list4 
                                    for m in list5 
                                    for n in list6 
                                    for o in list7
                                    for p in list8] 

    # printing result 
#     print ("All possible permutations are : " +  str(res))
    return res

In [11]:
class style:
    BOLD = '\033[1m'
    END = '\033[0m'

In [12]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from statistics import mean

def gridsearch(params):
    max_sens = 0
    max_spes = 0
    max_acc = 0
    best_params = []
    max_params = []
    max_auc = 0
    combs = compute_comb(params)
    print(len(combs))
    for j in range(len(combs)):
        print(j)
        accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,combs[j])
        if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
            print(combs[j])
            print (style.BOLD + 'accuracy    ' + style.END, mean(accuracy))
            print (style.BOLD + 'specificity ' + style.END, mean(specificity))
            print (style.BOLD + 'sensitivity ' + style.END, mean(sensitivity))
            print (style.BOLD + 'auc         ' + style.END, mean(auc))
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
        else:
            print(combs[j])
            print("accuracy    ",mean(accuracy))
            print("specificity ",mean(specificity))
            print("sensitivity ",mean(sensitivity))
            print("auc         ",mean(auc))
        best_params.append([combs[j],mean(accuracy),mean(specificity),mean(sensitivity),mean(auc)])
        if mean(auc)> max_auc:
            max_sens = mean(sensitivity)
            max_spes = mean(specificity)
            max_acc = mean(accuracy)
            max_auc = mean(auc)
            max_params = combs[j]
    return max_sens, max_params, max_spes, max_acc, max_auc, best_params

# Ratio = 1

In [15]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[1,2,3,4],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3]
        }


Στην συνέχεια τρέχουμε την gridsearch και εμφανίζουμε όλα τα αποτελέσματα. Μεταξύ γραμμών και με bold τυπώνονται οι τιμές που ικανοπούν τις συνθήκες:
    mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:

In [16]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

20736
0
[0.1, 1, 100, 1, 0, 0.5, 1, 1]
accuracy     0.5857142857142857
specificity  0.5799396681749622
sensitivity  0.655
auc          0.6174698340874811
1
[0.1, 1, 100, 1, 0, 0.5, 1, 2]
accuracy     0.25357142857142856
specificity  0.20614630467571643
sensitivity  0.855
auc          0.5305731523378582
2
[0.1, 1, 100, 1, 0, 0.5, 1, 3]
accuracy     0.11785714285714285
specificity  0.05784313725490196
sensitivity  0.88
auc          0.468921568627451
3
[0.1, 1, 100, 1, 0, 0.5, 1.5, 1]
accuracy     0.5839285714285715
specificity  0.5837481146304676
sensitivity  0.58
auc          0.5818740573152338
4
[0.1, 1, 100, 1, 0, 0.5, 1.5, 2]
accuracy     0.24285714285714285
specificity  0.19457013574660634
sensitivity  0.855
auc          0.5247850678733031
5
[0.1, 1, 100, 1, 0, 0.5, 1.5, 3]
accuracy     0.1125
specificity  0.052073906485671194
sensitivity  0.88
auc          0.4660369532428356
6
[0.1, 1, 100, 1, 0, 0.5, 2, 1]
accuracy     0.5839285714285715
specificity  0.5818250377073907
sensitivity

[0.1, 1, 100, 1, 1, 0.5, 1, 2]
accuracy     0.23928571428571427
specificity  0.19076168929110104
sensitivity  0.855
auc          0.5228808446455505
56
[0.1, 1, 100, 1, 1, 0.5, 1, 3]
accuracy     0.11607142857142858
specificity  0.05592006033182504
sensitivity  0.88
auc          0.46796003016591253
57
[0.1, 1, 100, 1, 1, 0.5, 1.5, 1]
accuracy     0.575
specificity  0.5780542986425339
sensitivity  0.53
auc          0.554027149321267
58
[0.1, 1, 100, 1, 1, 0.5, 1.5, 2]
accuracy     0.23214285714285715
specificity  0.1830316742081448
sensitivity  0.855
auc          0.5190158371040724
59
[0.1, 1, 100, 1, 1, 0.5, 1.5, 3]
accuracy     0.1125
specificity  0.052073906485671194
sensitivity  0.88
auc          0.4660369532428356
60
[0.1, 1, 100, 1, 1, 0.5, 2, 1]
accuracy     0.5732142857142857
specificity  0.578054298642534
sensitivity  0.505
auc          0.541527149321267
61
[0.1, 1, 100, 1, 1, 0.5, 2, 2]
accuracy     0.225
specificity  0.17526395173453999
sensitivity  0.855
auc          0.515131

[0.1, 1, 100, 2, 0.5, 0.5, 1, 3]
accuracy     0.12678571428571428
specificity  0.06557315233785822
sensitivity  0.905
auc          0.4852865761689291
111
[0.1, 1, 100, 2, 0.5, 0.5, 1.5, 1]
accuracy     0.5696428571428571
specificity  0.5683634992458522
sensitivity  0.58
auc          0.5741817496229261
112
[0.1, 1, 100, 2, 0.5, 0.5, 1.5, 2]
accuracy     0.2517857142857143
specificity  0.2023001508295626
sensitivity  0.88
auc          0.5411500754147813
113
[0.1, 1, 100, 2, 0.5, 0.5, 1.5, 3]
accuracy     0.1232142857142857
specificity  0.06168929110105581
sensitivity  0.905
auc          0.4833446455505279
114
[0.1, 1, 100, 2, 0.5, 0.5, 2, 1]
accuracy     0.5696428571428571
specificity  0.5702488687782805
sensitivity  0.555
auc          0.5626244343891402
115
[0.1, 1, 100, 2, 0.5, 0.5, 2, 2]
accuracy     0.23928571428571427
specificity  0.18883861236802413
sensitivity  0.88
auc          0.534419306184012
116
[0.1, 1, 100, 2, 0.5, 0.5, 2, 3]
accuracy     0.11428571428571428
specificity  0.

[0.1, 1, 100, 3, 0, 0.5, 1.5, 1]
accuracy     0.5482142857142858
specificity  0.5470965309200604
sensitivity  0.555
auc          0.5510482654600302
166
[0.1, 1, 100, 3, 0, 0.5, 1.5, 2]
accuracy     0.24642857142857144
specificity  0.20041478129713425
sensitivity  0.83
auc          0.5152073906485671
167
[0.1, 1, 100, 3, 0, 0.5, 1.5, 3]
accuracy     0.13035714285714287
specificity  0.06561085972850679
sensitivity  0.955
auc          0.5103054298642534
168
[0.1, 1, 100, 3, 0, 0.5, 2, 1]
accuracy     0.5517857142857143
specificity  0.5509803921568628
sensitivity  0.555
auc          0.5529901960784314
169
[0.1, 1, 100, 3, 0, 0.5, 2, 2]
accuracy     0.24821428571428572
specificity  0.20037707390648568
sensitivity  0.855
auc          0.5276885369532428
170
[0.1, 1, 100, 3, 0, 0.5, 2, 3]
accuracy     0.12142857142857143
specificity  0.055995475113122174
sensitivity  0.955
auc          0.505497737556561
171
[0.1, 1, 100, 3, 0, 0.75, 1, 1]
accuracy     0.5482142857142858
specificity  0.54521116

[0.1, 1, 100, 3, 1, 0.5, 1.5, 2]
accuracy     0.23035714285714287
specificity  0.17918552036199095
sensitivity  0.88
auc          0.5295927601809954
221
[0.1, 1, 100, 3, 1, 0.5, 1.5, 3]
accuracy     0.125
specificity  0.05984162895927602
sensitivity  0.955
auc          0.507420814479638
222
[0.1, 1, 100, 3, 1, 0.5, 2, 1]
accuracy     0.5732142857142857
specificity  0.5740573152337858
sensitivity  0.555
auc          0.5645286576168929
223
[0.1, 1, 100, 3, 1, 0.5, 2, 2]
accuracy     0.22142857142857142
specificity  0.16953242835595778
sensitivity  0.88
auc          0.5247662141779789
224
[0.1, 1, 100, 3, 1, 0.5, 2, 3]
accuracy     0.11785714285714285
specificity  0.05214932126696833
sensitivity  0.955
auc          0.5035746606334841
225
[0.1, 1, 100, 3, 1, 0.75, 1, 1]
accuracy     0.5625
specificity  0.5625188536953243
sensitivity  0.555
auc          0.5587594268476621
226
[0.1, 1, 100, 3, 1, 0.75, 1, 2]
accuracy     0.23214285714285715
specificity  0.18103318250377073
sensitivity  0.88


...

[0.4, 4, 400, 2, 0, 1.0, 1, 2]
accuracy     0.4892857142857143
specificity  0.475867269984917
sensitivity  0.66
auc          0.5679336349924585
20513
[0.4, 4, 400, 2, 0, 1.0, 1, 3]
accuracy     0.44642857142857145
specificity  0.42956259426847665
sensitivity  0.66
auc          0.5447812971342383
20514
[0.4, 4, 400, 2, 0, 1.0, 1.5, 1]
accuracy     0.5589285714285714
specificity  0.5528657616892911
sensitivity  0.635
auc          0.5939328808446456
20515
[0.4, 4, 400, 2, 0, 1.0, 1.5, 2]
accuracy     0.4982142857142857
specificity  0.48548265460030166
sensitivity  0.66
auc          0.5727413273001508
20516
[0.4, 4, 400, 2, 0, 1.0, 1.5, 3]
accuracy     0.4589285714285714
specificity  0.4392156862745098
sensitivity  0.71
auc          0.5746078431372549
20517
[0.4, 4, 400, 2, 0, 1.0, 2, 1]
accuracy     0.5696428571428571
specificity  0.5664027149321267
sensitivity  0.61
auc          0.5882013574660634
20518
[0.4, 4, 400, 2, 0, 1.0, 2, 2]
accuracy     0.5017857142857143
specificity  0.4892911

[0.4, 4, 400, 2, 1, 1.0, 1, 2]
accuracy     0.4232142857142857
specificity  0.3986802413273001
sensitivity  0.735
auc          0.5668401206636501
20567
[0.4, 4, 400, 2, 1, 1.0, 1, 3]
accuracy     0.3839285714285714
specificity  0.3467948717948718
sensitivity  0.855
auc          0.6008974358974359
20568
[0.4, 4, 400, 2, 1, 1.0, 1.5, 1]
accuracy     0.5625
specificity  0.5607843137254902
sensitivity  0.585
auc          0.5728921568627451
20569
[0.4, 4, 400, 2, 1, 1.0, 1.5, 2]
accuracy     0.41785714285714287
specificity  0.3892156862745098
sensitivity  0.785
auc          0.587107843137255
20570
[0.4, 4, 400, 2, 1, 1.0, 1.5, 3]
accuracy     0.3625
specificity  0.32364253393665154
sensitivity  0.855
auc          0.5893212669683258
20571
[0.4, 4, 400, 2, 1, 1.0, 2, 1]
accuracy     0.5892857142857143
specificity  0.5896681749622926
sensitivity  0.585
auc          0.5873340874811463
20572
[0.4, 4, 400, 2, 1, 1.0, 2, 2]
accuracy     0.41785714285714287
specificity  0.3853695324283559
sensitivi

[0.4, 4, 400, 3, 0.5, 1.0, 1, 2]
accuracy     0.4160714285714286
specificity  0.38721719457013576
sensitivity  0.78
auc          0.5836085972850679
20621
[0.4, 4, 400, 3, 0.5, 1.0, 1, 3]
accuracy     0.3892857142857143
specificity  0.3506787330316742
sensitivity  0.88
auc          0.6153393665158371
20622
[0.4, 4, 400, 3, 0.5, 1.0, 1.5, 1]
accuracy     0.5642857142857143
specificity  0.5567496229260935
sensitivity  0.66
auc          0.6083748114630467
20623
[0.4, 4, 400, 3, 0.5, 1.0, 1.5, 2]
accuracy     0.41785714285714287
specificity  0.3891025641025641
sensitivity  0.78
auc          0.584551282051282
20624
[0.4, 4, 400, 3, 0.5, 1.0, 1.5, 3]
accuracy     0.3535714285714286
specificity  0.31783559577677223
sensitivity  0.805
auc          0.5614177978883861
20625
[0.4, 4, 400, 3, 0.5, 1.0, 2, 1]
accuracy     0.5678571428571428
specificity  0.5606711915535445
sensitivity  0.66
auc          0.6103355957767722
20626
[0.4, 4, 400, 3, 0.5, 1.0, 2, 2]
accuracy     0.4107142857142857
specific

[0.4, 4, 400, 4, 0, 1.0, 1, 3]
accuracy     0.41964285714285715
specificity  0.3929864253393665
sensitivity  0.76
auc          0.5764932126696832
20676
[0.4, 4, 400, 4, 0, 1.0, 1.5, 1]
accuracy     0.5482142857142858
specificity  0.5489441930618402
sensitivity  0.54
auc          0.5444720965309201
20677
[0.4, 4, 400, 4, 0, 1.0, 1.5, 2]
accuracy     0.4517857142857143
specificity  0.4295248868778281
sensitivity  0.735
auc          0.5822624434389141
20678
[0.4, 4, 400, 4, 0, 1.0, 1.5, 3]
accuracy     0.4125
specificity  0.38721719457013576
sensitivity  0.735
auc          0.5611085972850678
20679
[0.4, 4, 400, 4, 0, 1.0, 2, 1]
accuracy     0.5517857142857143
specificity  0.556711915535445
sensitivity  0.49
auc          0.5233559577677225
20680
[0.4, 4, 400, 4, 0, 1.0, 2, 2]
accuracy     0.4392857142857143
specificity  0.41794871794871796
sensitivity  0.71
auc          0.563974358974359
20681
[0.4, 4, 400, 4, 0, 1.0, 2, 3]
accuracy     0.40714285714285714
specificity  0.3833333333333333
s

[0.4, 4, 400, 4, 1, 1.0, 1.5, 1]
accuracy     0.5446428571428571
specificity  0.5434012066365007
sensitivity  0.565
auc          0.5542006033182504
20731
[0.4, 4, 400, 4, 1, 1.0, 1.5, 2]
accuracy     0.32857142857142857
specificity  0.28695324283559576
sensitivity  0.855
auc          0.5709766214177979
20732
[0.4, 4, 400, 4, 1, 1.0, 1.5, 3]
accuracy     0.27321428571428574
specificity  0.22914781297134237
sensitivity  0.83
auc          0.5295739064856712
20733
[0.4, 4, 400, 4, 1, 1.0, 2, 1]
accuracy     0.5607142857142857
specificity  0.5625565610859729
sensitivity  0.54
auc          0.5512782805429864
20734
[0.4, 4, 400, 4, 1, 1.0, 2, 2]
accuracy     0.3142857142857143
specificity  0.27337858220211164
sensitivity  0.83
auc          0.5516892911010558
20735
[0.4, 4, 400, 4, 1, 1.0, 2, 3]
accuracy     0.26071428571428573
specificity  0.2119155354449472
sensitivity  0.88
auc          0.5459577677224736


In [17]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.3, 4, 100, 1, 0.5, 1.0, 1, 2]
0.49107142857142855
0.4642533936651584
0.835
0.6496266968325792


In [19]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.645 :
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.3, 4, 100, 1, 0.5, 1.0, 1, 2]
accuracy : 0.49107142857142855
spes     : 0.4642533936651584
sens     : 0.835
auc      : 0.6496266968325792
------------------------------------------------
parameters : [0.3, 4, 200, 1, 0.5, 1.0, 1, 2]
accuracy : 0.49107142857142855
spes     : 0.4642533936651584
sens     : 0.835
auc      : 0.6496266968325792
------------------------------------------------
parameters : [0.3, 4, 200, 3, 0, 1.0, 2, 1]
accuracy : 0.5910714285714286
spes     : 0.5818250377073907
sens     : 0.71
auc      : 0.6459125188536953
------------------------------------------------
parameters : [0.3, 4, 300, 1, 0.5, 1.0, 1, 2]
accuracy : 0.49107142857142855
spes     : 0.4642533936651584
sens     : 0.835
auc      : 0.6496266968325792
------------------------------------------------
parameters : [0.3, 4, 400, 1, 0.5, 1.0, 1, 2]
accuracy : 0.49107142857142855
spes     : 0.4642533936651584
sens     : 0.835
auc      : 0.6496266968325792
--------------------------------------